In [1]:
import numpy as np
import pandas as pd
import lightgbm as lgb
from sklearn.model_selection import StratifiedKFold, train_test_split
from sklearn.metrics import accuracy_score
from sklearn.decomposition import PCA
import matplotlib.pyplot as plt
import optuna

pd.set_option('max_columns', 300)

In [2]:
df_train = pd.read_csv('../train.csv')
df_train

row_id     A0T0G0C10      A0T0G1C9  A0T0G2C8  A0T0G3C7  A0T0G4C6  \
0            0 -9.536743e-07 -9.536743e-06 -0.000043 -0.000114 -0.000200   
1            1 -9.536743e-07 -9.536743e-06 -0.000043  0.000886 -0.000200   
2            2 -9.536743e-07 -1.536743e-06  0.000007  0.000129  0.000268   
3            3  4.632568e-08 -5.536743e-06  0.000012  0.000245  0.000492   
4            4 -9.536743e-07 -9.536743e-06 -0.000043 -0.000114 -0.000200   
...        ...           ...           ...       ...       ...       ...   
199995  199995 -9.536743e-07  4.632568e-07 -0.000003  0.000176  0.000350   
199996  199996 -9.536743e-07 -9.536743e-06 -0.000043 -0.000114 -0.000200   
199997  199997  4.632568e-08  1.463257e-06 -0.000005 -0.000031 -0.000019   
199998  199998 -9.536743e-07 -9.536743e-06 -0.000043 -0.000114 -0.000200   
199999  199999  1.046326e-06 -1.536743e-06  0.000069  0.000539  0.001329   

        A0T0G5C5  A0T0G6C4  A0T0G7C3  A0T0G8C2      A0T0G9C1     A0T0G10C0  \
0      -0.000240 -0.000200 -0.000114 -0.000043 -9.536743e-06 -9.536743e-07   
1       0.000760 -0.000200 -0.000114 -0.000043 -9.536743e-06 -9.536743e-07   
2       0.000270  0.000243  0.000125  0.000001 -6.536743e-06  4.632568e-08   
3       0.000522  0.000396  0.000197 -0.000003 -6.536743e-06 -9.536743e-07   
4      -0.000240 -0.000200 -0.000114 -0.000043 -9.536743e-06 -9.536743e-07   
...          ...       ...       ...       ...           ...           ...   
199995  0.000290  0.000200  0.000206 -0.000023 -9.536743e-06 -9.536743e-07   
199996 -0.000240 -0.000200 -0.000114 -0.000043 -9.536743e-06 -9.536743e-07   
199997 -0.000037 -0.000037 -0.000015 -0.000005 -7.536743e-06 -9.536743e-07   
199998 -0.000240 -0.000200 -0.000114 -0.000043 -9.536743e-06 -9.536743e-07   
199999  0.001657  0.001328  0.000520  0.000063 -5.367432e-07 -9.536743e-07   

            A0T1G0C9      A0T1G1C8  A0T1G2C7  A0T1G3C6  A0T1G4C5  A0T1G5C4  \
0      -9.536743e-06 -8.583069e-05 -0.000343 -0.000801 -0.001202 -0.001202   
1      -9.536743e-06 -8.583069e-05 -0.000343  0.000199 -0.000202  0.001798   
2      -3.536743e-06  1.693115e-07  0.000008  0.000366  0.000766  0.000937   
3      -9.536743e-06 -1.783069e-05  0.000068  0.000722  0.001594  0.001913   
4      -9.536743e-06 -8.583069e-05 -0.000343 -0.000801 -0.001202 -0.001202   
...              ...           ...       ...       ...       ...       ...   
199995  4.632568e-07  4.169312e-06  0.000087  0.000729  0.001448  0.001338   
199996 -9.536743e-06 -8.583069e-05 -0.000343 -0.000801 -0.001202  0.000798   
199997 -3.536743e-06 -6.830688e-06 -0.000086 -0.000145 -0.000283 -0.000270   
199998  9.904633e-04 -8.583069e-05 -0.000343 -0.000801 -0.001202  0.001798   
199999 -7.536743e-06 -1.583069e-05  0.000343  0.002105  0.004791  0.005343   

        A0T1G6C3  A0T1G7C2  A0T1G8C1  A0T1G9C0      A0T2G0C8  A0T2G1C7  \
0      -0.000801 -0.000343 -0.000086 -0.000010 -4.291534e-05 -0.000343   
1      -0.000801 -0.000343 -0.000086 -0.000010 -4.291534e-05 -0.000343   
2       0.000632  0.000101 -0.000021 -0.000008  8.465576e-08 -0.000080   
3       0.001111  0.000247 -0.000047 -0.000010 -1.891534e-05 -0.000138   
4      -0.000801 -0.000343 -0.000086 -0.000010 -4.291534e-05 -0.000343   
...          ...       ...       ...       ...           ...       ...   
199995  0.000859  0.000207 -0.000006 -0.000010  7.084656e-06 -0.000063   
199996 -0.000801 -0.000343 -0.000086 -0.000010 -4.291534e-05 -0.000343   
199997 -0.000174 -0.000075 -0.000016 -0.000008  2.084656e-06 -0.000094   
199998 -0.000801 -0.000343 -0.000086 -0.000010 -4.291534e-05 -0.000343   
199999  0.002974  0.000642 -0.000002 -0.000010 -9.915344e-06  0.000025   

        A0T2G2C6  A0T2G3C5  A0T2G4C4  A0T2G5C3  A0T2G6C2  A0T2G7C1  A0T2G8C0  \
0      -0.001202 -0.002403 -0.003004 -0.002403 -0.001202 -0.000343 -0.000043   
1       0.001798 -0.000403  0.001996  0.003597 -0.001202 -0.000343 -0.000043   
2       0.000114  0.000710  0.001307  0.001065  0.000375 -0.000017 -0.000017   
3       0.00

In [3]:
df_test = pd.read_csv('../test.csv')
df_test

row_id     A0T0G0C10  A0T0G1C9      A0T0G2C8  A0T0G3C7  A0T0G4C6  \
0      200000 -9.536743e-07 -0.000002 -9.153442e-07  0.000024  0.000034   
1      200001 -9.536743e-07 -0.000010 -4.291534e-05 -0.000114  0.001800   
2      200002  4.632568e-08  0.000003  8.465576e-08 -0.000014  0.000007   
3      200003 -9.536743e-07 -0.000008  8.084656e-06  0.000216  0.000420   
4      200004 -9.536743e-07 -0.000010 -4.291534e-05 -0.000114 -0.000200   
...       ...           ...       ...           ...       ...       ...   
99995  299995 -9.536743e-07 -0.000008 -4.291534e-05 -0.000108 -0.000194   
99996  299996 -9.536743e-07 -0.000010 -4.291534e-05 -0.000114 -0.000200   
99997  299997 -9.536743e-07 -0.000010 -4.291534e-05 -0.000114 -0.000200   
99998  299998 -9.536743e-07 -0.000010 -4.291534e-05 -0.000114 -0.000200   
99999  299999 -9.536743e-07 -0.000009 -3.991534e-05 -0.000111 -0.000195   

       A0T0G5C5  A0T0G6C4  A0T0G7C3  A0T0G8C2  A0T0G9C1     A0T0G10C0  \
0     -0.000002  0.000021  0.000024 -0.000009 -0.000008 -9.536743e-07   
1     -0.000240  0.001800 -0.000114  0.000957 -0.000010 -9.536743e-07   
2     -0.000005 -0.000004  0.000003  0.000004 -0.000008 -9.536743e-07   
3      0.000514  0.000452  0.000187 -0.000005 -0.000008  4.632568e-08   
4     -0.000240 -0.000200 -0.000114 -0.000043 -0.000010 -9.536743e-07   
...         ...       ...       ...       ...       ...           ...   
99995 -0.000234 -0.000195 -0.000110 -0.000043 -0.000010 -9.536743e-07   
99996 -0.000240 -0.000200 -0.000114 -0.000043 -0.000010 -9.536743e-07   
99997 -0.000240 -0.000200 -0.000114 -0.000043 -0.000010 -9.536743e-07   
99998 -0.000240 -0.000200 -0.000114 -0.000043 -0.000010 -9.536743e-07   
99999 -0.000238 -0.000189 -0.000110 -0.000042 -0.000010 -9.536743e-07   

       A0T1G0C9  A0T1G1C8  A0T1G2C7  A0T1G3C6  A0T1G4C5  A0T1G5C4  A0T1G6C3  \
0     -0.000003 -0.000017 -0.000074  0.000038  0.000068  0.000164  0.000180   
1     -0.000010 -0.000086 -0.000343  0.001199  0.001798  0.000798  0.000199   
2     -0.000003 -0.000003 -0.000045 -0.000038 -0.000110 -0.000127 -0.000076   
3     -0.000006 -0.000024  0.000060  0.000712  0.001579  0.001887  0.001299   
4     -0.000010 -0.000086 -0.000343 -0.000801 -0.001202 -0.000202 -0.000801   
...         ...       ...       ...       ...       ...       ...       ...   
99995 -0.000010 -0.000083 -0.000325 -0.000749 -0.001135 -0.001133 -0.000752   
99996 -0.000010 -0.000086 -0.000343 -0.000801 -0.001202 -0.001202 -0.000801   
99997  0.000990 -0.000086 -0.000343 -0.000801 -0.001202  0.001798 -0.000801   
99998 -0.000010 -0.000086 -0.000343 -0.000801 -0.001202 -0.001202 -0.000801   
99999 -0.000009 -0.000076 -0.000321 -0.000745 -0.001127 -0.001120 -0.000743   

       A0T1G7C2  A0T1G8C1  A0T1G9C0  A0T2G0C8  A0T2G1C7  A0T2G2C6  A0T2G3C5  \
0     -0.000003 -0.000025 -0.000009  0.000004 -0.000101 -0.000171  0.000006   
1      0.000657 -0.000086 -0.000010 -0.000043 -0.000343 -0.001202  0.001597   
2     -0.000012 -0.000004 -0.000005  0.000009 -0.000052 -0.000110 -0.000280   
3      0.000203 -0.000041 -0.000009 -0.000016 -0.000128  0.000128  0.001283   
4     -0.000343 -0.000086 -0.000010 -0.000043 -0.000343 -0.001202 -0.000403   
...         ...       ...       ...       ...       ...       ...       ...   
99995 -0.000317 -0.000077 -0.000010 -0.000029 -0.000288 -0.001007 -0.002031   
99996 -0.000343 -0.000086 -0.000010 -0.000043 -0.000343 -0.001202 -0.002403   
99997 -0.000343 -0.000086 -0.000010 -0.000043 -0.000343  0.000798 -0.000403   
99998 -0.000343 -0.000086 -0.000010 -0.000043 -0.000343 -0.001202  0.007597   
99999 -0.000314 -0.000079 -0.000010 -0.000035 -0.000306 -0.001046 -0.002073   

       A0T2G4C4  A0T2G5C3  A0T2G6C2  A0T2G7C1  A0T2G8C0  A0T3G0C7  A0T3G1C6  \
0      0.000330  0.000580  0.000228 -0.000015 -0.000016 -0.000026 -0.000146   
1      0.002996 -0.002403  0.000798 -0.000343 -0.000043 -0.000114 -0.000801   
2     -0.000220 -0.000165 -0.000048 -0.000023 -0.000005 -0.000006 -0.000073   
3      0.002351

In [4]:
df_sample_submission = pd.read_csv('../sample_submission.csv')
df_sample_submission

row_id                    target
0      200000  Streptococcus_pneumoniae
1      200001  Streptococcus_pneumoniae
2      200002  Streptococcus_pneumoniae
3      200003  Streptococcus_pneumoniae
4      200004  Streptococcus_pneumoniae
...       ...                       ...
99995  299995  Streptococcus_pneumoniae
99996  299996  Streptococcus_pneumoniae
99997  299997  Streptococcus_pneumoniae
99998  299998  Streptococcus_pneumoniae
99999  299999  Streptococcus_pneumoniae

[100000 rows x 2 columns]

In [5]:
df_train['target'].value_counts()

Bacteroides_fragilis        20139
Streptococcus_pyogenes      20076
Streptococcus_pneumoniae    20074
Campylobacter_jejuni        20063
Salmonella_enterica         20030
Escherichia_coli            19958
Enterococcus_hirae          19947
Escherichia_fergusonii      19937
Staphylococcus_aureus       19929
Klebsiella_pneumoniae       19847
Name: target, dtype: int64

In [6]:
target_values, target_keys = pd.Series(df_train['target'].unique()).factorize()
key2val = dict(zip(target_keys, target_values))
val2key = dict(zip(target_values, target_keys))
df_train['target'] = df_train['target'].replace(key2val)
df_train

row_id     A0T0G0C10      A0T0G1C9  A0T0G2C8  A0T0G3C7  A0T0G4C6  \
0            0 -9.536743e-07 -9.536743e-06 -0.000043 -0.000114 -0.000200   
1            1 -9.536743e-07 -9.536743e-06 -0.000043  0.000886 -0.000200   
2            2 -9.536743e-07 -1.536743e-06  0.000007  0.000129  0.000268   
3            3  4.632568e-08 -5.536743e-06  0.000012  0.000245  0.000492   
4            4 -9.536743e-07 -9.536743e-06 -0.000043 -0.000114 -0.000200   
...        ...           ...           ...       ...       ...       ...   
199995  199995 -9.536743e-07  4.632568e-07 -0.000003  0.000176  0.000350   
199996  199996 -9.536743e-07 -9.536743e-06 -0.000043 -0.000114 -0.000200   
199997  199997  4.632568e-08  1.463257e-06 -0.000005 -0.000031 -0.000019   
199998  199998 -9.536743e-07 -9.536743e-06 -0.000043 -0.000114 -0.000200   
199999  199999  1.046326e-06 -1.536743e-06  0.000069  0.000539  0.001329   

        A0T0G5C5  A0T0G6C4  A0T0G7C3  A0T0G8C2      A0T0G9C1     A0T0G10C0  \
0      -0.000240 -0.000200 -0.000114 -0.000043 -9.536743e-06 -9.536743e-07   
1       0.000760 -0.000200 -0.000114 -0.000043 -9.536743e-06 -9.536743e-07   
2       0.000270  0.000243  0.000125  0.000001 -6.536743e-06  4.632568e-08   
3       0.000522  0.000396  0.000197 -0.000003 -6.536743e-06 -9.536743e-07   
4      -0.000240 -0.000200 -0.000114 -0.000043 -9.536743e-06 -9.536743e-07   
...          ...       ...       ...       ...           ...           ...   
199995  0.000290  0.000200  0.000206 -0.000023 -9.536743e-06 -9.536743e-07   
199996 -0.000240 -0.000200 -0.000114 -0.000043 -9.536743e-06 -9.536743e-07   
199997 -0.000037 -0.000037 -0.000015 -0.000005 -7.536743e-06 -9.536743e-07   
199998 -0.000240 -0.000200 -0.000114 -0.000043 -9.536743e-06 -9.536743e-07   
199999  0.001657  0.001328  0.000520  0.000063 -5.367432e-07 -9.536743e-07   

            A0T1G0C9      A0T1G1C8  A0T1G2C7  A0T1G3C6  A0T1G4C5  A0T1G5C4  \
0      -9.536743e-06 -8.583069e-05 -0.000343 -0.000801 -0.001202 -0.001202   
1      -9.536743e-06 -8.583069e-05 -0.000343  0.000199 -0.000202  0.001798   
2      -3.536743e-06  1.693115e-07  0.000008  0.000366  0.000766  0.000937   
3      -9.536743e-06 -1.783069e-05  0.000068  0.000722  0.001594  0.001913   
4      -9.536743e-06 -8.583069e-05 -0.000343 -0.000801 -0.001202 -0.001202   
...              ...           ...       ...       ...       ...       ...   
199995  4.632568e-07  4.169312e-06  0.000087  0.000729  0.001448  0.001338   
199996 -9.536743e-06 -8.583069e-05 -0.000343 -0.000801 -0.001202  0.000798   
199997 -3.536743e-06 -6.830688e-06 -0.000086 -0.000145 -0.000283 -0.000270   
199998  9.904633e-04 -8.583069e-05 -0.000343 -0.000801 -0.001202  0.001798   
199999 -7.536743e-06 -1.583069e-05  0.000343  0.002105  0.004791  0.005343   

        A0T1G6C3  A0T1G7C2  A0T1G8C1  A0T1G9C0      A0T2G0C8  A0T2G1C7  \
0      -0.000801 -0.000343 -0.000086 -0.000010 -4.291534e-05 -0.000343   
1      -0.000801 -0.000343 -0.000086 -0.000010 -4.291534e-05 -0.000343   
2       0.000632  0.000101 -0.000021 -0.000008  8.465576e-08 -0.000080   
3       0.001111  0.000247 -0.000047 -0.000010 -1.891534e-05 -0.000138   
4      -0.000801 -0.000343 -0.000086 -0.000010 -4.291534e-05 -0.000343   
...          ...       ...       ...       ...           ...       ...   
199995  0.000859  0.000207 -0.000006 -0.000010  7.084656e-06 -0.000063   
199996 -0.000801 -0.000343 -0.000086 -0.000010 -4.291534e-05 -0.000343   
199997 -0.000174 -0.000075 -0.000016 -0.000008  2.084656e-06 -0.000094   
199998 -0.000801 -0.000343 -0.000086 -0.000010 -4.291534e-05 -0.000343   
199999  0.002974  0.000642 -0.000002 -0.000010 -9.915344e-06  0.000025   

        A0T2G2C6  A0T2G3C5  A0T2G4C4  A0T2G5C3  A0T2G6C2  A0T2G7C1  A0T2G8C0  \
0      -0.001202 -0.002403 -0.003004 -0.002403 -0.001202 -0.000343 -0.000043   
1       0.001798 -0.000403  0.001996  0.003597 -0.001202 -0.000343 -0.000043   
2       0.000114  0.000710  0.001307  0.001065  0.000375 -0.000017 -0.000017   
3       0.00

In [7]:
df_train.corr()

row_id  A0T0G0C10  A0T0G1C9  A0T0G2C8  A0T0G3C7  A0T0G4C6  \
row_id     1.000000  -0.000480  0.000862  0.001132  0.002983 -0.000901   
A0T0G0C10 -0.000480   1.000000 -0.000668 -0.001438 -0.003359 -0.002266   
A0T0G1C9   0.000862  -0.000668  1.000000  0.000018  0.003200  0.002519   
A0T0G2C8   0.001132  -0.001438  0.000018  1.000000  0.088412  0.060144   
A0T0G3C7   0.002983  -0.003359  0.003200  0.088412  1.000000  0.119712   
...             ...        ...       ...       ...       ...       ...   
A9T0G0C1  -0.001713   0.000835 -0.004690 -0.008022 -0.021595 -0.030779   
A9T0G1C0  -0.003474   0.000289 -0.005256 -0.012159 -0.030539 -0.039987   
A9T1G0C0   0.001021   0.002480 -0.004585 -0.011668  0.007061 -0.021889   
A10T0G0C0 -0.002749  -0.000850 -0.001549 -0.003477 -0.008799 -0.011281   
target    -0.002469   0.000055  0.024334  0.036950  0.071534  0.130634   

           A0T0G5C5  A0T0G6C4  A0T0G7C3  A0T0G8C2  A0T0G9C1  A0T0G10C0  \
row_id     0.003380  0.000806  0.001082  0.000616 -0.002085  -0.001289   
A0T0G0C10 -0.001151 -0.003384  0.002306 -0.001764 -0.000283   0.001276   
A0T0G1C9   0.000618  0.003464  0.008319 -0.000554 -0.000561  -0.000239   
A0T0G2C8   0.023778  0.020243  0.016196  0.009146 -0.000500  -0.002027   
A0T0G3C7   0.173624  0.125264  0.085270  0.053888  0.006604  -0.004806   
...             ...       ...       ...       ...       ...        ...   
A9T0G0C1  -0.029835 -0.029315 -0.026245 -0.012286 -0.002189   0.010732   
A9T0G1C0  -0.041230 -0.039232 -0.029629 -0.012845 -0.002627   0.013735   
A9T1G0C0  -0.029368 -0.005358 -0.028037 -0.015938 -0.002208   0.010234   
A10T0G0C0 -0.011864 -0.010963 -0.008724 -0.003555 -0.000887  -0.000197   
target     0.184245  0.153690  0.081811  0.036566  0.012491  -0.015857   

           A0T1G0C9  A0T1G1C8  A0T1G2C7  A0T1G3C6  A0T1G4C5  A0T1G5C4  \
row_id    -0.000441  0.002258 -0.003513  0.002228  0.002166  0.000931   
A0T0G0C10 -0.003264 -0.003187 -0.001873 -0.005834 -0.001747 -0.004100   
A0T0G1C9  -0.007432  0.007360  0.000691  0.001567  0.044874 -0.001726   
A0T0G2C8  -0.015645  0.013068  0.115226  0.025698  0.047694  0.027334   
A0T0G3C7  -0.034800  0.047455  0.055459  0.143901  0.223178  0.188099   
...             ...       ...       ...       ...       ...       ...   
A9T0G0C1  -0.023353 -0.019191 -0.025305 -0.043735 -0.049909 -0.057091   
A9T0G1C0  -0.028346 -0.017922 -0.032597 -0.056970 -0.067764 -0.078799   
A9T1G0C0  -0.027320 -0.020339 -0.031644 -0.036358 -0.043157 -0.065106   
A10T0G0C0 -0.009963 -0.004111 -0.008646 -0.009064 -0.019141 -0.020246   
target     0.001797  0.050863  0.093948  0.130783  0.207351  0.195878   

           A0T1G6C3  A0T1G7C2  A0T1G8C1  A0T1G9C0  A0T2G0C8  A0T2G1C7  \
row_id    -0.004156 -0.002486  0.003343  0.002813  0.001969  0.001766   
A0T0G0C10 -0.003655 -0.002662 -0.002784  0.000798 -0.002258 -0.000415   
A0T0G1C9   0.002107  0.000472  0.004888  0.002020  0.005904  0.001072   
A0T0G2C8   0.049452  0.016313  0.010618  0.000926  0.005759  0.006975   
A0T0G3C7   0.197951  0.152456  0.049013 -0.002643  0.023286  0.035332   
...             ...       ...       ...       ...       ...       ...   
A9T0G0C1  -0.040777 -0.029552 -0.014716  0.004618 -0.008681 -0.017929   
A9T0G1C0  -0.044391 -0.038414 -0.016521  0.006873 -0.013737 -0.023534   
A9T1G0C0  -0.045252 -0.036480 -0.018394  0.018131 -0.014975 -0.027707   
A10T0G0C0 -0.017419 -0.007474  0.001785 -0.002097 -0.002053  0.002312   
target     0.164826  0.091320  0.050295 -0.011608  0.051393  0.053521   

           A0T2G2C6  A0T2G3C5  A0T2G4C4  A0T2G5C3  A0T2G6C2  A0T2G7C1  \
row_id     0.001564 -0.001532  0.001296  0.002773  0.000519 -0.000977   
A0T0G0C10 -0.005834 -0.005259 -0.006627 -0.006180 -0.004649 -0.002442   
A0T0G1C9   0.110062 -0.003932 -0.005885  0.042837 -0.000715  0.000082   
A0T0G2C8   0.036888  0.064665  0.057831  0.071580  0.040093  0.032865   
A0T0G3C7   0.091388  0.154585  0.220523  0.190370  0.168688  0.048118   
...             ...       ...       ...    

In [8]:
df_train, df_val = train_test_split(df_train, stratify=df_train['target'], test_size=0.2, shuffle=True, random_state=0)
df_train.index = range(len(df_train))
df_val.index = range(len(df_val))

In [9]:
class LGBModel:
    def __init__(self):
        self.models = None
        self.num_folds = None
        self.is_prob = False
        self.num_classes = None

    def fit(self, x, y, num_folds=5, is_plot=False, is_prob=False, seed=0):
        self.num_classes = len(np.unique(y))
        self.is_prob = is_prob
        if is_prob:
            preds = np.zeros((len(x), self.num_classes))
        else:
            preds = np.zeros(len(x))
        self.models = []
        self.num_folds = num_folds
        
        kfold = StratifiedKFold(n_splits=num_folds, shuffle=True, random_state=seed)
        for fold, (trn_ind, val_ind) in enumerate(kfold.split(x, y)):
            x_train, y_train = x.loc[trn_ind], y.loc[trn_ind]
            x_val, y_val = x.loc[val_ind], y.loc[val_ind]

            model = lgb.LGBMClassifier()
            model.fit(x_train, y_train)
            if is_prob:
                preds[val_ind] = model.predict_proba(x_val)
            else:
                preds[val_ind] = model.predict(x_val)
                print(f'current_fold: {fold+1}, accuracy: {accuracy_score(y_val, preds[val_ind])}')
            
            self.models.append(model)

        if not is_prob:    
            print(f'Full predictions accuracy: {accuracy_score(y, preds)}')

        if is_plot:
            ax = lgb.plot_importance(self.models[0], max_num_features=50, figsize=(16, 16))
            plt.show()
    
        return preds
    
    def predict(self, x):
        if self.is_prob:
            preds = np.zeros((len(x), self.num_classes))
        else:
            preds = np.zeros(len(x))
        
        for model in self.models:
            if self.is_prob:
                preds += model.predict_proba(x)
            else:
                preds += model.predict(x)
        
        if self.is_prob:
            return preds / self.num_folds
        else:
            return np.round(preds / self.num_folds)

In [10]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader


class NewReprNN(nn.Module):
    def __init__(self, input_size, num_classes, dataset_size, hidden_dim=2):
        super(NewReprNN, self).__init__()
        self.input_size = input_size
        self.hidden_dim = hidden_dim
        self.fc1 = nn.Linear(1, hidden_dim)
        self.fc2 = nn.Linear(input_size*hidden_dim, num_classes)
        self.relu = nn.ReLU()
        self.new_repr = torch.zeros((dataset_size, input_size*hidden_dim))
        self.current_pos = 0
    
    def forward(self, x):
        batch_size = x.shape[0]
        out = self.relu(self.fc1(x.reshape(-1, 1))).reshape(batch_size, -1)
        
        self.new_repr[self.current_pos:self.current_pos+batch_size] = out.detach()
        self.current_pos += batch_size
        
        return self.fc2(out)
    
    def get_new_repr(self):
        return self.new_repr.cpu().numpy()
    
    def reset_new_repr(self, dataset_size):
        self.new_repr = torch.zeros((dataset_size, self.input_size*self.hidden_dim))
        self.current_pos = 0


class NewReprDataset(Dataset):
    def __init__(self, x, y):
        super(NewReprDataset, self).__init__()
        self.x = x
        self.y = y
    
    def __len__(self):
        return len(self.x)
    
    def __getitem__(self, index):
        x = torch.tensor(self.x[index])
        y = torch.tensor(self.y[index])
        
        return x.float(), y


class NewReprModel:
    def __init__(self):
        self.models = None
        self.num_folds = None
        self.device = 'cpu'#'cuda' if torch.cuda.is_available() else 'cpu'
        self.num_classes = None
    
    def fit(self, x, y, num_folds=5, batch_size=16, lr=3e-4, epochs=1, seed=0):
        self.num_folds = num_folds
        self.models = []
        self.lgb_models = []
        self.num_classes = len(np.unique(y.values))
        
        criterion = nn.CrossEntropyLoss()
        
        nn_preds_full = np.zeros((len(x), self.num_classes))
        lgb_preds_full = np.zeros((len(x), self.num_classes))
        
        kfold = StratifiedKFold(n_splits=self.num_folds, shuffle=True, random_state=seed)
        for fold, (trn_ind, val_ind) in enumerate(kfold.split(x, y)):
            x_train, y_train = x.loc[trn_ind].values, y.loc[trn_ind].values
            x_val, y_val = x.loc[val_ind].values, y.loc[val_ind].values
            
            model = NewReprNN(input_size=x_train.shape[1], num_classes=self.num_classes, dataset_size=len(x_train)).to(self.device)
            lgb_model = lgb.LGBMClassifier()
            
            optimizer = optim.Adam(params=model.parameters(), lr=lr)
            
            dataset_train = NewReprDataset(x_train, y_train)
            loader_train = DataLoader(dataset=dataset_train, shuffle=False, batch_size=batch_size)
            
            dataset_val = NewReprDataset(x_val, y_val)
            loader_val = DataLoader(dataset=dataset_val, shuffle=False, batch_size=batch_size)
            
            print(f'\n\ncurrent_fold: {fold+1}')
            
            for epoch in range(epochs):
                preds_arr = np.zeros((x_val.shape[0], self.num_classes))
                targets_arr = np.zeros(y_val.shape[0])
                model.reset_new_repr(dataset_size=len(x_train))
                new_repr = None
                current_pos = 0
                model.train()
                for data, target in loader_train:
                    data = data.to(self.device)
                    target = target.to(self.device)
                    
                    preds = model(data)
                    loss = criterion(preds, target)
                    
                    optimizer.zero_grad()
                    loss.backward()
                    optimizer.step()
                
                if epoch+1 == epochs:
                    print('LGB training start')
                    new_repr = model.get_new_repr()
                    self.lgb_models.append(lgb_model)
                    self.lgb_models[fold].fit(new_repr, y_train)
                    print('LGB training end')
                
                model.reset_new_repr(dataset_size=len(x_val))
                
                with torch.no_grad():
                    model.eval()
                    for data, target in loader_val:
                        data = data.to(self.device)
                        target = target.to(self.device)

                        preds = model(data)
                        preds_arr[current_pos:current_pos+preds.shape[0]] = preds.cpu().numpy()
                        targets_arr[current_pos:current_pos+preds.shape[0]] = target.cpu().numpy()
                        current_pos += preds.shape[0]

                    if epoch+1 == epochs:
                        print('LGB validation start')
                        new_repr = model.get_new_repr()
                        lgb_preds_full[val_ind] = self.lgb_models[fold].predict_proba(new_repr)
                        nn_preds_full[val_ind] = preds_arr
                        print('LGB validation end')
                    
                print(f'Epoch: {epoch+1}')
            
            self.models.append(model)
            
        return nn_preds_full, lgb_preds_full
    
    def predict(self, x):
        with torch.no_grad():
            x = np.array(x)
            preds = np.zeros((x.shape[0], self.num_classes))
            lgb_preds = np.zeros((x.shape[0], self.num_classes))
            x = torch.tensor(x).float().to(self.device)
            for i in range(self.num_folds):
                self.models[i].eval()
                self.models[i].reset_new_repr(dataset_size=x.shape[0])
                preds += self.models[i](x).cpu().numpy()

                new_repr = self.models[i].get_new_repr()
                lgb_preds += self.lgb_models[i].predict_proba(new_repr)

            return preds / self.num_folds, lgb_preds / self.num_folds

In [11]:
class Pipeline:
    def __init__(self):
        self.new_repr_model = None
        self.dim_standard_model = None
        self.dim_reduced_model = None
        self.pca = None
        
        self.dim_standard_preds = None
        self.dim_reduced_preds = None
        self.dim_increased_preds = None
        self.nn_preds = None
        
        self.num_classes = None
        self.target = None
        
        self.dim_reduced_weights = None
        self.dim_increased_weights = None
        self.dim_standard_weights = None
        self.nn_weights = None
    
    def objective(self, trial):
        dim_reduced_trial = []
        dim_increased_trial = []
        dim_standard_trial = []
        nn_trial = []
        for i in range(self.num_classes):
            dim_reduced_trial.append(trial.suggest_float(f'dim_reduced_weights{i+1}', 0.0, 1.0))
            dim_increased_trial.append(trial.suggest_float(f'dim_increased_weights{i+1}', 0.0, 1.0))
            dim_standard_trial.append(trial.suggest_float(f'dim_standard_weights{i+1}', 0.0, 1.0))
            nn_trial.append(trial.suggest_float(f'nn_weights{i+1}', 0.0, 1.0))
        
        all_weights_cols = []
        for i in range(self.num_classes):
            all_weights_cols.append(
                dim_reduced_trial[i] + dim_increased_trial[i] + dim_standard_trial[i] + nn_trial[i]
            )
        all_weights = sum(all_weights_cols)
        
        preds_probs = np.zeros((len(self.nn_preds), self.num_classes))
        
        self.dim_reduced_weights = []
        self.dim_increased_weights = []
        self.dim_standard_weights = []
        self.nn_weights = []
        for i in range(self.num_classes):
            self.dim_reduced_weights.append(dim_reduced_trial[i]/all_weights_cols[i]/all_weights)
            self.dim_increased_weights.append(dim_increased_trial[i]/all_weights_cols[i]/all_weights)
            self.dim_standard_weights.append(dim_standard_trial[i]/all_weights_cols[i]/all_weights)
            self.nn_weights.append(nn_trial[i]/all_weights_cols[i]/all_weights)
            
            preds_probs[:, i] = self.dim_reduced_preds[:, i]*self.dim_reduced_weights[i] \
                              + self.dim_increased_preds[:, i]*self.dim_increased_weights[i] \
                              + self.dim_standard_preds[:, i]*self.dim_standard_weights[i] \
                              + self.nn_preds[:, i]*self.nn_weights[i]
        
        preds = np.argmax(preds_probs, axis=1)
        
        return accuracy_score(self.target, preds)
    
    def fit(self, data):
        
        self.target = data['target']
        
        columns = [f'col{i+1}' for i in range(180)]
        decomposed_data = pd.DataFrame()
        decomposed_data.index = data.index
        self.pca = PCA(n_components=180)
        decomposed_data.loc[:, columns] = self.pca.fit_transform(data.drop(['row_id', 'target'], axis=1))

        self.dim_reduced_model = LGBModel()
        self.dim_reduced_preds = self.dim_reduced_model.fit(decomposed_data, data['target'], is_plot=False, is_prob=True)
        
        self.dim_standard_model = LGBModel()
        self.dim_standard_preds = self.dim_standard_model.fit(data.drop(['target', 'row_id'], axis=1), data['target'], is_plot=False, is_prob=True)
        
        self.new_repr_model = NewReprModel()
        self.nn_preds, self.dim_increased_preds = self.new_repr_model.fit(data.drop(['row_id', 'target'], axis=1), data['target'])
        
        self.num_classes = self.nn_preds.shape[1]
        
        study = optuna.create_study(direction="maximize")
        study.optimize(self.objective, n_trials=2000)
        p = study.best_trial.params
        
        all_weights_cols = []
        for i in range(self.num_classes):
            all_weights_cols.append(
                p[f'dim_reduced_weights{i+1}'] + p[f'dim_increased_weights{i+1}'] \
                + p[f'dim_standard_weights{i+1}'] + p[f'nn_weights{i+1}']
            )
        all_weights = sum(all_weights_cols)
        
        self.dim_reduced_weights = []
        self.dim_increased_weights = []
        self.dim_standard_weights = []
        self.nn_weights = []
        for i in range(self.num_classes):
            self.dim_reduced_weights.append(p[f'dim_reduced_weights{i+1}']/all_weights_cols[i]/all_weights)
            self.dim_increased_weights.append(p[f'dim_increased_weights{i+1}']/all_weights_cols[i]/all_weights)
            self.dim_standard_weights.append(p[f'dim_standard_weights{i+1}']/all_weights_cols[i]/all_weights)
            self.nn_weights.append(p[f'nn_weights{i+1}']/all_weights_cols[i]/all_weights)
    
    def predict(self, x):
        dim_reduced_preds = self.dim_reduced_model.predict(self.pca.transform(x))
        dim_standard_preds = self.dim_standard_model.predict(x)
        nn_preds, dim_increased_preds = self.new_repr_model.predict(x)
        
        preds_probs = np.zeros((len(nn_preds), self.num_classes))
        
        for i in range(self.num_classes):
            preds_probs[:, i] = dim_reduced_preds[:, i]*self.dim_reduced_weights[i] \
                              + dim_increased_preds[:, i]*self.dim_increased_weights[i] \
                              + dim_standard_preds[:, i]*self.dim_standard_weights[i] \
                              + nn_preds[:, i]*self.nn_weights[i]
        
        preds = np.argmax(preds_probs, axis=1)
        
        return preds

In [12]:
pipe = Pipeline()
pipe.fit(df_train)



current_fold: 1
LGB training start
LGB training end
LGB validation start
LGB validation end
Epoch: 1


current_fold: 2
LGB training start
LGB training end
LGB validation start
LGB validation end
Epoch: 1


current_fold: 3
LGB training start
LGB training end
LGB validation start
LGB validation end
Epoch: 1


current_fold: 4
LGB training start
LGB training end
LGB validation start
LGB validation end
Epoch: 1


current_fold: 5
LGB training start
LGB training end
LGB validation start


[I 2022-02-13 19:19:18,071] A new study created in memory with name: no-name-c51b15b1-167d-42cf-8ca0-ea5366a71e9e
[I 2022-02-13 19:19:18,139] Trial 0 finished with value: 0.96760625 and parameters: {'dim_reduced_weights1': 0.10744881533768957, 'dim_increased_weights1': 0.045678788291313666, 'dim_standard_weights1': 0.4924912073682054, 'nn_weights1': 0.6302671807304987, 'dim_reduced_weights2': 0.09880385596234675, 'dim_increased_weights2': 0.5141479170342651, 'dim_standard_weights2': 0.3775093813798791, 'nn_weights2': 0.645324445501336, 'dim_reduced_weights3': 0.12205039210674629, 'dim_increased_weights3': 0.39656944652465376, 'dim_standard_weights3': 0.6833562626580486, 'nn_weights3': 0.6640167754748206, 'dim_reduced_weights4': 0.5310339707218891, 'dim_increased_weights4': 0.395787103158764, 'dim_standard_weights4': 0.007908699899402905, 'nn_weights4': 0.3851238907261263, 'dim_reduced_weights5': 0.7764472927627989, 'dim_increased_weights5': 0.7948232265479109, 'dim_standard_weights5': 

LGB validation end
Epoch: 1


[I 2022-02-13 19:19:18,273] Trial 2 finished with value: 0.9741625 and parameters: {'dim_reduced_weights1': 0.06732230093794989, 'dim_increased_weights1': 0.6218936917807718, 'dim_standard_weights1': 0.42915300444654114, 'nn_weights1': 0.6047123311865646, 'dim_reduced_weights2': 0.5178444311534084, 'dim_increased_weights2': 0.07316869947555282, 'dim_standard_weights2': 0.43399898263260606, 'nn_weights2': 0.7419697050546169, 'dim_reduced_weights3': 0.6877120306348973, 'dim_increased_weights3': 0.4239188495421651, 'dim_standard_weights3': 0.9731090354135052, 'nn_weights3': 0.7984872369642255, 'dim_reduced_weights4': 0.6096983662478593, 'dim_increased_weights4': 0.7241104214272125, 'dim_standard_weights4': 0.8672381317947653, 'nn_weights4': 0.6585731841982044, 'dim_reduced_weights5': 0.3608194316311045, 'dim_increased_weights5': 0.7650519716176762, 'dim_standard_weights5': 0.3100055361757822, 'nn_weights5': 0.26344110430905876, 'dim_reduced_weights6': 0.8489643978002664, 'dim_increased_we

[I 2022-02-13 19:19:18,605] Trial 7 finished with value: 0.96684375 and parameters: {'dim_reduced_weights1': 0.04382271413600225, 'dim_increased_weights1': 0.9797814745097946, 'dim_standard_weights1': 0.23096080069714964, 'nn_weights1': 0.6110897397056586, 'dim_reduced_weights2': 0.4672715008806315, 'dim_increased_weights2': 0.23728288860204094, 'dim_standard_weights2': 0.3410866207375135, 'nn_weights2': 0.25716381319163606, 'dim_reduced_weights3': 0.1984100429238197, 'dim_increased_weights3': 0.07315155533978213, 'dim_standard_weights3': 0.3817972081696498, 'nn_weights3': 0.5026344333163345, 'dim_reduced_weights4': 0.8349790250437427, 'dim_increased_weights4': 0.9782215569885108, 'dim_standard_weights4': 0.8200069026907338, 'nn_weights4': 0.6431535471373997, 'dim_reduced_weights5': 0.8961351156372024, 'dim_increased_weights5': 0.5756594702527146, 'dim_standard_weights5': 0.0203921332767657, 'nn_weights5': 0.009535881575656546, 'dim_reduced_weights6': 0.3779950066956529, 'dim_increased

...

[I 2022-02-13 19:30:28,497] Trial 1977 finished with value: 0.98539375 and parameters: {'dim_reduced_weights1': 0.9607204340847414, 'dim_increased_weights1': 0.15139785003909745, 'dim_standard_weights1': 0.3626644120475331, 'nn_weights1': 0.140302826844295, 'dim_reduced_weights2': 0.946786072148976, 'dim_increased_weights2': 0.17505212102179044, 'dim_standard_weights2': 0.2795447124969385, 'nn_weights2': 0.050807218422108925, 'dim_reduced_weights3': 0.4740977332660821, 'dim_increased_weights3': 0.22376428445009794, 'dim_standard_weights3': 0.5674254097362945, 'nn_weights3': 0.021784140188199814, 'dim_reduced_weights4': 0.7083644428543661, 'dim_increased_weights4': 0.015288425523387134, 'dim_standard_weights4': 0.8297278841569772, 'nn_weights4': 0.24419845995235323, 'dim_reduced_weights5': 0.6578063848644315, 'dim_increased_weights5': 0.18327762936891495, 'dim_standard_weights5': 0.92412794839338, 'nn_weights5': 0.9824339060524564, 'dim_reduced_weights6': 0.891633241154069, 'dim_increas

[I 2022-02-13 19:30:31,306] Trial 1982 finished with value: 0.9854125 and parameters: {'dim_reduced_weights1': 0.979773057455452, 'dim_increased_weights1': 0.15135251820721518, 'dim_standard_weights1': 0.3579227150916178, 'nn_weights1': 0.10970525153112462, 'dim_reduced_weights2': 0.9255607659354583, 'dim_increased_weights2': 0.14436229499279854, 'dim_standard_weights2': 0.25296096116207606, 'nn_weights2': 0.0656644175350555, 'dim_reduced_weights3': 0.4649001971671662, 'dim_increased_weights3': 0.22316221549706142, 'dim_standard_weights3': 0.5785948266621475, 'nn_weights3': 0.03540747243617026, 'dim_reduced_weights4': 0.7252129416677714, 'dim_increased_weights4': 0.0035697915733248764, 'dim_standard_weights4': 0.8202574642276693, 'nn_weights4': 0.22292655800716535, 'dim_reduced_weights5': 0.6568225902368189, 'dim_increased_weights5': 0.19831320712058526, 'dim_standard_weights5': 0.9375101142001436, 'nn_weights5': 0.9692386983637856, 'dim_reduced_weights6': 0.9218604940478595, 'dim_incr

[I 2022-02-13 19:30:34,069] Trial 1987 finished with value: 0.9846875 and parameters: {'dim_reduced_weights1': 0.9828752055438675, 'dim_increased_weights1': 0.16958625357411453, 'dim_standard_weights1': 0.39339560990530087, 'nn_weights1': 0.10976974947701382, 'dim_reduced_weights2': 0.9242558880111459, 'dim_increased_weights2': 0.1628687370685589, 'dim_standard_weights2': 0.2958138709748355, 'nn_weights2': 0.48341617423031713, 'dim_reduced_weights3': 0.3955230559734707, 'dim_increased_weights3': 0.2668045918488207, 'dim_standard_weights3': 0.5643389788209955, 'nn_weights3': 0.062280746096572456, 'dim_reduced_weights4': 0.7672965503385678, 'dim_increased_weights4': 0.04571658172638943, 'dim_standard_weights4': 0.8697441154908963, 'nn_weights4': 0.22451031520135836, 'dim_reduced_weights5': 0.6126524499981996, 'dim_increased_weights5': 0.223314421031, 'dim_standard_weights5': 0.9179861022370077, 'nn_weights5': 0.9824427778737992, 'dim_reduced_weights6': 0.938964373959143, 'dim_increased_w

[I 2022-02-13 19:30:36,966] Trial 1992 finished with value: 0.98515 and parameters: {'dim_reduced_weights1': 0.9497017326301145, 'dim_increased_weights1': 0.1638809477536089, 'dim_standard_weights1': 0.23174030901910803, 'nn_weights1': 0.13146056249910062, 'dim_reduced_weights2': 0.9160474253057267, 'dim_increased_weights2': 0.1624791265457418, 'dim_standard_weights2': 0.21652113036253626, 'nn_weights2': 0.0781404946606378, 'dim_reduced_weights3': 0.4063448322416686, 'dim_increased_weights3': 0.27366992673254575, 'dim_standard_weights3': 0.6489133491479506, 'nn_weights3': 0.03736992628086418, 'dim_reduced_weights4': 0.7357824457822343, 'dim_increased_weights4': 0.022074087890760135, 'dim_standard_weights4': 0.8755621107332449, 'nn_weights4': 0.2499036453486706, 'dim_reduced_weights5': 0.6285255912940184, 'dim_increased_weights5': 0.20642009199896522, 'dim_standard_weights5': 0.9641595223274045, 'nn_weights5': 0.9489859890792852, 'dim_reduced_weights6': 0.9439905836022253, 'dim_increase

[I 2022-02-13 19:30:39,761] Trial 1997 finished with value: 0.98440625 and parameters: {'dim_reduced_weights1': 0.04348059626981188, 'dim_increased_weights1': 0.14964499094450523, 'dim_standard_weights1': 0.40054289438558804, 'nn_weights1': 0.11434530971979884, 'dim_reduced_weights2': 0.9516801552079487, 'dim_increased_weights2': 0.12365538534796945, 'dim_standard_weights2': 0.297694177609274, 'nn_weights2': 0.04822397010699286, 'dim_reduced_weights3': 0.3535099937206647, 'dim_increased_weights3': 0.2274211465969464, 'dim_standard_weights3': 0.551427188889596, 'nn_weights3': 0.06438876293271088, 'dim_reduced_weights4': 0.6808341985705212, 'dim_increased_weights4': 0.044268898282613225, 'dim_standard_weights4': 0.8590816907627598, 'nn_weights4': 0.23685101990207322, 'dim_reduced_weights5': 0.6154569471173433, 'dim_increased_weights5': 0.18363497788770383, 'dim_standard_weights5': 0.9274584440514929, 'nn_weights5': 0.9278344209053281, 'dim_reduced_weights6': 0.9061660419133907, 'dim_incr

In [13]:
# Ensemble models performance

preds = pipe.predict(df_val.drop(['row_id', 'target'], axis=1))
print('\nValidation dataset accuracy')
accuracy_score(df_val['target'], preds)


Validation dataset accuracy


0.9898

In [14]:
# Standard model performance

model = LGBModel()
model.fit(df_train.drop(['target', 'row_id'], axis=1), df_train['target'])
preds = model.predict(df_val.drop(['target', 'row_id'], axis=1))
print('\nValidation dataset accuracy')
accuracy_score(df_val['target'], preds)

current_fold: 1, accuracy: 0.9775625
current_fold: 2, accuracy: 0.9759375
current_fold: 3, accuracy: 0.97665625
current_fold: 4, accuracy: 0.9784375
current_fold: 5, accuracy: 0.97709375
Full predictions accuracy: 0.9771375

Validation dataset accuracy


0.96405

In [ ]:
# Standard model performance with dimensionality reduced dataset

columns =[f'col{i+1}' for i in range(180)]
decomposed_train = pd.DataFrame()
decomposed_train.index = df_train.index
decomposed_test = pd.DataFrame()
decomposed_test.index = df_test.index
pca = PCA(n_components=180)
decomposed_train.loc[:, columns] = pca.fit_transform(df_train.drop(['row_id', 'target'], axis=1))
decomposed_test.loc[:, columns] = pca.transform(df_test.drop('row_id', axis=1))

model = LGBModel()
model.fit(decomposed_train, df_train['target'])
preds = model.predict(pca.transform(df_val.drop(['target', 'row_id'], axis=1)))
print('\nValidation dataset accuracy')
accuracy_score(df_val['target'], preds)

current_fold: 1, accuracy: 0.97990625
current_fold: 2, accuracy: 0.97784375
current_fold: 3, accuracy: 0.98078125
current_fold: 4, accuracy: 0.98059375


In [ ]:
"""submission_df = df_test[['row_id']]
submission_df['target'] = model.predict(decomposed_test)
submission_df['target'] = submission_df['target'].replace(val2key)
submission_df.to_csv('submission.csv', index=False)"""